Raw data and code from https://drive.google.com/drive/folders/1Jsv34JjNo22NOCd26iBHMP80EPG0xmQE, linked from Casey Handmer's blog post [Solar and batteries for generic use cases](https://caseyhandmer.wordpress.com/2024/11/09/solar-and-batteries-for-generic-use-cases/)

In [1]:
from datetime import datetime
from pathlib import Path
from random import uniform

import altair as alt
from numba import njit
import pandas as pd
from vega_datasets import data

alt.data_transformers.enable("vegafusion")

folder = Path('./texas')
folder.exists()

True

In [2]:
actual = [fp for fp in folder.iterdir() if fp.stem.startswith('Actual')]
actual

[PosixPath('texas/Actual_36.05_-102.95_2006_UPV_17MW_5_Min.csv'),
 PosixPath('texas/Actual_34.05_-102.05_2006_UPV_151MW_5_Min.csv'),
 PosixPath('texas/Actual_34.95_-101.85_2006_DPV_27MW_5_Min.csv'),
 PosixPath('texas/Actual_33.45_-94.45_2006_DPV_27MW_5_Min.csv'),
 PosixPath('texas/Actual_33.45_-94.35_2006_DPV_27MW_5_Min.csv'),
 PosixPath('texas/Actual_35.85_-102.85_2006_UPV_17MW_5_Min.csv'),
 PosixPath('texas/Actual_35.05_-101.85_2006_DPV_27MW_5_Min.csv'),
 PosixPath('texas/Actual_33.15_-102.25_2006_UPV_50MW_5_Min.csv'),
 PosixPath('texas/Actual_35.35_-101.95_2006_UPV_67MW_5_Min.csv'),
 PosixPath('texas/Actual_32.55_-102.75_2006_UPV_118MW_5_Min.csv'),
 PosixPath('texas/Actual_32.45_-94.85_2006_DPV_35MW_5_Min.csv'),
 PosixPath('texas/Actual_33.15_-94.65_2006_UPV_14MW_5_Min.csv'),
 PosixPath('texas/Actual_34.55_-102.55_2006_UPV_168MW_5_Min.csv'),
 PosixPath('texas/Actual_33.55_-101.85_2006_DPV_37MW_5_Min.csv'),
 PosixPath('texas/Actual_32.35_-94.25_2006_UPV_122MW_5_Min.csv'),
 PosixPath(

In [3]:
states = alt.topo_feature(data.us_10m.url, feature='states')

usa_states = alt.Chart(states).mark_geoshape(
    fill='lightgray',
    stroke='white'
).project('albersUsa').properties(
    width=500,
    height=300
)
usa_states

alt.Chart(...)

In [4]:
def stem_to_lat_lon(s: str) -> tuple[float, float]:
    return tuple(float(x) for x in s.split('_')[1:3])

df = pd.DataFrame([stem_to_lat_lon(fp.stem) for fp in actual], columns=['lat', 'lon'])

usa_states + alt.Chart(df).mark_circle().encode(
    longitude='lon:Q',
    latitude='lat:Q',
    size=alt.value(10),
).project(
    'albersUsa'
).properties(width=500, height=300)

alt.LayerChart(...)

In [5]:
raw = pd.read_csv(folder / 'Actual_36.25_-102.95_2006_UPV_84MW_5_Min.csv')
raw['local_time'] = raw['LocalTime'].apply(lambda s: datetime.strptime(s, '%m/%d/%y %H:%M'))
raw['power'] = raw['Power(MW)']
raw = raw.drop(columns=['LocalTime', 'Power(MW)'])
raw.head()

local_time  power
0 2006-01-01 00:00:00    0.0
1 2006-01-01 00:05:00    0.0
2 2006-01-01 00:10:00    0.0
3 2006-01-01 00:15:00    0.0
4 2006-01-01 00:20:00    0.0

In [6]:
raw.describe()

local_time          power
count                         105120  105120.000000
mean   2006-07-02 11:57:29.999999744      16.039188
min              2006-01-01 00:00:00       0.000000
25%              2006-04-02 05:58:45       0.000000
50%              2006-07-02 11:57:30       0.000000
75%              2006-10-01 17:56:15      32.600000
max              2006-12-31 23:55:00      84.000000
std                              NaN      22.735229

In [7]:
jan_1st = raw.loc[(raw['local_time'].dt.day == 1) & (raw['local_time'].dt.month == 1)]
alt.Chart(jan_1st).mark_line().encode(x='local_time', y='power', tooltip='local_time').properties(width=500)

alt.Chart(...)

In [8]:
from datetime import date
day_avg = raw.groupby(raw['local_time'].dt.time).mean().drop(columns=['local_time']).reset_index()
day_avg['local_time'] = day_avg['local_time'].apply(lambda t: datetime.combine(date.today(), t))
alt.Chart(day_avg).mark_line().encode(x='local_time', y='power').properties(title="Average power generation over a day")

alt.Chart(...)

In [9]:
from datetime import time

year_avg = raw.groupby(raw['local_time'].dt.date).mean().drop(columns=['local_time']).reset_index()
year_avg['local_time'] = year_avg['local_time'].apply(lambda t: datetime.combine(t, time(12, 0, 0)))
alt.Chart(year_avg).mark_line().encode(
    x='local_time', y='power'
).properties(height=500, width=800)

alt.Chart(...)

In [10]:
sol = raw.copy()
sol['power'] /= 84  # 84 MW array, standardize on 1MW
sol['power'].mean(), len(sol)

(np.float64(0.1909427094658259), 105120)

In [11]:
sol.head()

local_time  power
0 2006-01-01 00:00:00    0.0
1 2006-01-01 00:05:00    0.0
2 2006-01-01 00:10:00    0.0
3 2006-01-01 00:15:00    0.0
4 2006-01-01 00:20:00    0.0

In [12]:
alt.Chart(sol).mark_line().encode(
    x='local_time', y='power'
).properties(
    width=800, height=600
)

alt.Chart(...)

In [13]:
days = raw['local_time'].dt.date.unique()[::10]
df = raw.loc[raw['local_time'].dt.date.isin(days)].assign(
    day=lambda x: x['local_time'].dt.date.apply(lambda y: datetime.combine(y, time(12, 0, 0))),
    time=lambda x: x['local_time'].dt.time.apply(lambda y: datetime.combine(date.today(), y)),
)
alt.Chart(df.sample(5000)).mark_line().encode(
    x="time:T",
    y="power:Q",
    color="day:N"
)

alt.Chart(...)

Time to implement the `uptime` function. We baseline a 1MW array, then set up numerical array with loads of different sizes and batteries of different sizes. If the battery is empty, load is off. If battery is full, no chargning can occur. We measure everything in 5 minute intervals (according to the data), and assume the battery starts full.
Battery state is measure in MWh stored, so in each interval we have to divide by 12.

Let's start with a naive variant (no vectorization)

In [14]:
24*365

8760

In [15]:
# capacity in MWh, load in MW, sol in MW
@njit
def uptime(capacity: float, load: float, sol: list[float]) -> tuple[float, float, float, float]:
    battery: list[float] = [capacity] + [0.0 for _ in sol] # MWh
    utilization: list[float] = [0.0 for _ in sol]  # percentage
    t_interval = 24.0 * 365.0 / len(sol)  # hours
    for i in range(len(sol)):
        sol_interval: float = sol[i]
        remaining_load: float = (load - sol_interval)*t_interval
        if sol_interval > load:  # More sun than load
            utilization[i] = 1  # Can run full load
            excess_solar = sol_interval - load
            # if battery[i] < capacity:
                # battery[i+1] = battery[i] + t_interval*excess_solar
            battery[i+1] = min(battery[i] + t_interval*excess_solar, capacity)
            
        elif battery[i] > remaining_load: # Battery is full enough
            utilization[i] = 1
            battery[i+1] = battery[i] - remaining_load
        else: # Battery fully drained, cannot use all load
            utilization[i] = (sol_interval * t_interval + battery[i]) / (load * t_interval)  # equivalent: sol_interval / load + battery / (load * ts)
            battery[i+1] = 0

    batsum = 0
    for b in battery[:-1]:
        batsum += 1 if b > 0 else 0
        
    return (
        capacity,
        load,
        batsum / (len(battery) - 1),
        t_interval * sum(utilization) / (24 * 365),
    )

uptime(2.0, 1.0, sol['power'].tolist())

(2.0, 1.0, 0.00023782343987823439, 0.19117101996811398)

In [16]:
@njit
def all_in_system_cost(
    solar_cost: float, battery_cost: float, load_cost: float, battery_size: float, array_size: float, sol: list[float]
) -> float:
    capacity, load, battery_util, total_util = uptime(
        capacity=battery_size / array_size,
        load=1 / array_size,
        sol=sol,
    )
    return (capacity * battery_cost + solar_cost + load_cost * load) / (load * total_util)

all_in_system_cost(200_000, 200_000, 5_000_000, 10, 5, sol['power'].tolist())

10527576.740406122

Casey's number here is `1.0523e7`, so I'm going to call that close enough.
There appears to be a bug in Casey's implementation. The check if the battery can be charged happens at the start of the interval. If the battery is almost full this will be negative, but then there might be too much solar excess, filling the battery beyond max.  However, if we leave the bug in the program, the number doesn't match quite as closely... So either this bug is not in Casey's program, or my program has another discrepancy.

In [17]:
@njit
def cost_and_elasticity(
    solar_cost: float, battery_cost: float, load_cost: float, battery_size: float, array_size: float, sol: list[float]
) -> tuple[float, float, float, float, float]:
    size_to_cost = lambda b, a: all_in_system_cost(
        solar_cost, battery_cost, load_cost, b, a, sol
    )
    cost = size_to_cost(battery_size, array_size)
    cost_battery = size_to_cost(1.01*battery_size+0.01, array_size)
    cost_array = size_to_cost(battery_size, 1.01*array_size+0.01)
    return cost, cost_battery, cost_array, (cost - cost_battery) / cost, (cost - cost_array) / cost

cost_and_elasticity(200e3, 200e3, 5e6, 10, 5, sol['power'].tolist())

(10527576.740406122,
 10506720.226831798,
 10520210.612583503,
 0.0019811314691513676,
 0.0006996983260494161)

I'm running the gradient descent for more steps with a much smaller amplitude since this code appears to be ~1000 times faster than the equivalent Mathematica. This takes care of some numerical infelicities.

In [18]:
@njit
def find_minimum_system_cost(
    solar_cost: float,
    battery_cost: float,
    load_cost: float,
    sol: list[float],
) -> tuple[tuple[float, float, float], tuple[float, float, 1], tuple[float, float, float], tuple[float, float, float], any]:
    bi = min(10, 10 * load_cost / 5e6)
    ai = min(10, 10 * load_cost / 5e6)
    amplitude = 10 + 70 * (load_cost / 5e6)
    if 7e5 < load_cost < 13e5: amplitude *= 3
    if 80e6 < load_cost: amplitude *= 0.5

    cost_min = 10**10
    bi_min = bi
    ai_min = ai
    for i in range(100):
        # There was a bug here: cost_and_elasticity were getting called with wrong argument order
        # Changing them around doesn't affect the results since we always passed in the same number here
        cost, cost_bat, cost_arr, dcost_bat, dcost_arr = cost_and_elasticity(solar_cost, battery_cost, load_cost, bi, ai, sol)
        if cost < cost_min:
            ai_min, bi_min, cost_min = ai, bi, cost
        # if True: print((cost, cost_bat, cost_arr, dcost_bat, dcost_arr), bi, ai)
        bi = max(0, bi + amplitude * uniform(0.1, 1) * dcost_bat)
        ai = max(0.01, ai + amplitude * uniform(0.1, 1) * dcost_arr)

    ut = uptime(bi_min / ai_min, 1 / ai_min, sol)
    
    array_cost = solar_cost * ai_min
    storage_cost = battery_cost * bi_min
    total_cost = array_cost + storage_cost + load_cost
    
    return (
        (solar_cost, battery_cost, load_cost),
        (ai_min, bi_min, 1),
        (array_cost, storage_cost, load_cost),
        (array_cost + storage_cost, total_cost, total_cost / ut[-1]),
        ut
    )

find_minimum_system_cost(2e5, 2e5, 1e5, sol['power'].tolist())

((200000.0, 200000.0, 100000.0),
 (1.3960843186370024, 0.0, 1),
 (279216.8637274005, 0.0, 100000.0),
 (279216.8637274005, 379216.8637274005, 1448531.3901021087),
 (0.0, 0.7162891142393895, 0.0, 0.26179402553414394))

That's really not that far from Casey's outcomes. I'm going to chalk the difference up to order of operations and floating point shenanigans.

In [19]:
from tqdm import tqdm
results_raw = [
    find_minimum_system_cost(200e3, 200e3, 10e3*10**(0.1*i), sol['power'].tolist())
    for i in tqdm(range(40))
]

100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 40/40 [00:16<00:00,  2.38it/s]


I'm not sure what's taking Casey's implementation so long? Let's call this a minute, then it's a factor 100? Factor 1000 if I enable compilation with `numba`.


In [20]:
results_raw

[((200000.0, 200000.0, 10000.0),
  (1.2244353216573673, 0.0, 1),
  (244887.06433147346, 0.0, 10000.0),
  (244887.06433147346, 254887.06433147346, 1091908.353259966),
  (0.0, 0.8167029995887599, 0.0, 0.23343265354687595)),
 ((200000.0, 200000.0, 12589.254117941673),
  (1.2407553998584486, 0.0, 1),
  (248151.07997168973, 0.0, 12589.254117941673),
  (248151.07997168973, 260740.3340896314, 1102931.8827598882),
  (0.0, 0.8059606269810189, 0.0, 0.2364065616066658)),
 ((200000.0, 200000.0, 15848.931924611135),
  (1.2426763817356783, 0.0, 1),
  (248535.27634713566, 0.0, 15848.931924611135),
  (248535.27634713566, 264384.2082717468, 1116702.2814634265),
  (0.0, 0.8047147388471921, 0.0, 0.23675442654713136)),
 ((200000.0, 200000.0, 19952.623149688796),
  (1.2574119765816938, 0.0, 1),
  (251482.39531633875, 0.0, 19952.623149688796),
  (251482.39531633875, 271435.01846602757, 1133788.5699939742),
  (0.0, 0.7952842971311004, 0.0, 0.2394053226938689)),
 ((200000.0, 200000.0, 25118.8643150958),
  (1.

In [21]:
labels = [
    'solar cost ($/MW)', 'battery cost ($/MW)', 'load cost ($/MW)',
    'array size (MW)', 'battery size (MWh)', 'load size (1 MW by definition)',
    'array cost ($)', 'battery cost ($)', 'load cost ($, normalized to 1 MW)',
    'total power system cost ($)', 'total system cost ($)', 'total cost per utilization ($)',
    'battery size relative to 1 MW array', 'load size relative to 1 MW array', 'annual battery utilization', 'annual load utilization'
]

results = pd.DataFrame([dict(zip(labels, (x for tup in r for x in tup))) for r in results_raw])
results.head()

solar cost ($/MW)  battery cost ($/MW)  load cost ($/MW)  array size (MW)  \
0           200000.0             200000.0      10000.000000         1.224435   
1           200000.0             200000.0      12589.254118         1.240755   
2           200000.0             200000.0      15848.931925         1.242676   
3           200000.0             200000.0      19952.623150         1.257412   
4           200000.0             200000.0      25118.864315         1.274538   

   battery size (MWh)  load size (1 MW by definition)  array cost ($)  \
0                 0.0                               1   244887.064331   
1                 0.0                               1   248151.079972   
2                 0.0                               1   248535.276347   
3                 0.0                               1   251482.395316   
4                 0.0                               1   254907.585569   

   battery cost ($)  load cost ($, normalized to 1 MW)  \
0               0.0                       10000.000000   
1               0.0                       12589.254118   
2               0.0                       15848.931925   
3               0.0                       19952.623150   
4               0.0                       25118.864315   

   total power system cost ($)  total system cost ($)  \
0                244887.064331          254887.064331   
1                248151.079972          260740.334090   
2                248535.276347          264384.208272   
3                251482.395316          271435.018466   
4                254907.585569          280026.449884   

   total cost per utilization ($)  battery size relative to 1 MW array  \
0                    1.091908e+06                                  0.0   
1                    1.102932e+06                                  0.0   
2                    1.116702e+06                                  0.0   
3                    1.133789e+06                                  0.0   
4                    1.155046e+06                                  0.0   

   load size relative to 1 MW array  annual battery utilization  \
0                          0.816703                         0.0   
1                          0.805961                         0.0   
2                          0.804715                         0.0   
3                          0.795284                         0.0   
4                          0.784598                         0.0   

   annual load utilization  
0                 0.233433  
1                 0.236407  
2                 0.236754  
3                 0.239405  
4                 0.242438

In [22]:
subsystems = results.melt(id_vars='annual load utilization', value_vars=[
    'array cost ($)', 'battery cost ($)', 'load cost ($/MW)', 'total power system cost ($)', 'total system cost ($)', 
])
subsystems = subsystems.loc[subsystems['value'] <= 2e7]
alt.Chart(subsystems).mark_line().encode(
    x='annual load utilization:Q',
    y=alt.Y('value:Q', scale=alt.Scale(domain=[0, 2e7], clamp=True)),
    color='variable:N',
    tooltip='variable:N',
).properties(width=800, height=600)

alt.Chart(...)

In [23]:
subsystems = results.melt(id_vars="load cost ($/MW)", value_vars=[
    'array cost ($)', 'battery cost ($)', 'load cost ($/MW)', 'total power system cost ($)', 'total system cost ($)', 
    'total cost per utilization ($)',
])
subsystems = subsystems.loc[subsystems['value'] > 0]

alt.Chart(subsystems).mark_line().encode(
    x=alt.X('load cost ($/MW):Q', scale=alt.Scale(type='log', domain=[0.5e4, 1e8])),
    y=alt.Y('value:Q', scale=alt.Scale(type='log', domain=[0.5e3, 1e8])),
    color='variable:N',
    tooltip=('variable:N','value:Q'),
).properties(width=800, height=600)

alt.Chart(...)

In [24]:
alt.Chart(results).mark_line().encode(
    x=alt.X('load cost ($/MW)', scale=alt.Scale(type='log')),
    y='annual load utilization'
).properties(width=800, height=600)

alt.Chart(...)

In [25]:
results.describe()

solar cost ($/MW)  battery cost ($/MW)  load cost ($/MW)  \
count               40.0                 40.0      4.000000e+01   
mean            200000.0             200000.0      9.654325e+06   
std                  0.0                  0.0      1.851465e+07   
min             200000.0             200000.0      1.000000e+04   
25%             200000.0             200000.0      9.485821e+04   
50%             200000.0             200000.0      8.971641e+05   
75%             200000.0             200000.0      8.457462e+06   
max             200000.0             200000.0      7.943282e+07   

       array size (MW)  battery size (MWh)  load size (1 MW by definition)  \
count        40.000000           40.000000                            40.0   
mean          4.518091            5.870373                             1.0   
std           3.932988            6.983019                             0.0   
min           1.224435            0.000000                             1.0   
25%           1.389062            0.000000                             1.0   
50%           2.171273            0.081675                             1.0   
75%           7.296975           14.324511                             1.0   
max          14.579005           15.834358                             1.0   

       array cost ($)  battery cost ($)  load cost ($, normalized to 1 MW)  \
count    4.000000e+01      4.000000e+01                       4.000000e+01   
mean     9.036181e+05      1.174075e+06                       9.654325e+06   
std      7.865975e+05      1.396604e+06                       1.851465e+07   
min      2.448871e+05      0.000000e+00                       1.000000e+04   
25%      2.778124e+05      0.000000e+00                       9.485821e+04   
50%      4.342547e+05      1.633505e+04                       8.971641e+05   
75%      1.459395e+06      2.864902e+06                       8.457462e+06   
max      2.915801e+06      3.166872e+06                       7.943282e+07   

       total power system cost ($)  total system cost ($)  \
count                 4.000000e+01           4.000000e+01   
mean                  2.077693e+06           1.173202e+07   
std                   2.151899e+06           2.023223e+07   
min                   2.448871e+05           2.548871e+05   
25%                   2.778124e+05           3.726706e+05   
50%                   4.505897e+05           1.347754e+06   
75%                   4.324297e+06           1.278176e+07   
max                   6.082672e+06           8.551550e+07   

       total cost per utilization ($)  battery size relative to 1 MW array  \
count                    4.000000e+01                            40.000000   
mean                     1.311563e+07                             0.754919   
std                      2.006034e+07                             0.854375   
min                      1.091908e+06                             0.000000   
25%                      1.428868e+06                             0.000000   
50%                      4.104358e+06                             0.036685   
75%                      1.365009e+07                             1.630466   
max                      8.641906e+07                             2.171670   

       load size relative to 1 MW array  annual battery utilization  \
count                         40.000000                   40.000000   
mean                           0.433660                    0.420597   
std                            0.284317                    0.431302   
min                            0.068592                    0.000000   
25%                            0.137087                    0.000000   
50%                            0.461433                    0.241904   
75%                            0.719966                    0.928886   
max                            0.816703                    0.988898   

       annual load utilization  
count                40.000000  
mean                  0.546628  
std  

In [26]:
for col in ['array cost ($)', 'battery cost ($)', 'total power system cost ($)']:
    results[col.replace('$', '$/MWh')] = results[col] / (10 * 24 * 365 * results['annual load utilization'])

import numpy as np
min_util = results.loc[results['annual load utilization'].idxmin()]
uvals = np.arange(0.01, min_util['annual load utilization'], 0.001)
underutilized_solar = pd.Series(uvals, name='annual load utilization').to_frame()
underutilized_solar['variable'] = 'underutilized solar'
underutilized_solar['value'] = min_util['array cost ($)'] / (10 * 24 * 365 * uvals)

subsystems = results.melt(id_vars='annual load utilization', value_vars=[
    'array cost ($/MWh)', 'battery cost ($/MWh)', 'total power system cost ($/MWh)', 
])
subsystems = pd.concat([subsystems, underutilized_solar])
alt.Chart(subsystems).mark_line().encode(
    x='annual load utilization:Q',
    y=alt.Y('value:Q', scale=alt.Scale(domain=[0, 80])),
    color='variable:N',
).properties(width=800, height=600).interactive()

alt.Chart(...)